In [3]:
import gym
import numpy as np
import pygame
from gym import spaces
import pandas as pd

In [4]:
room_maze=[
        ['S','0','1','1','0','0','0','0','G','0','0'],
        ['0','0','0','0','0','1','0','1','1','1','0'],
        ['0','0','1','1','0','1','0','1','1','1','0'],
        ['1','0','1','1','0','1','0','G','0','0','0'],
        ['1','0','0','0','0','1','0','0','0','0','0']
    ]

In [5]:
class VacEnv(gym.Env):
    def __init__(self):
        self.room = np.array(room_maze)
        self.start = np.where(self.room == 'S')
        self.goal = np.where(self.room == 'G')
        self.current = self.start
        self.cell_size = 130  
        self.rows, self.cols = self.room.shape
        self.screen = pygame.display.set_mode((self.cols * self.cell_size, self.rows * self.cell_size))
        self.clock = pygame.time.Clock()
        self.action_space = spaces.Discrete(4) 
        self.observation_space = spaces.Tuple((spaces.Discrete(self.rows), spaces.Discrete(self.cols)))
        self.n_states=55
        self.visited=[]
      
    def reset(self):
        self.current=self.start
        return self.current
        return self.current
    def step(self,action):
      new_pos=np.array(self.current)
      if action==0:
        new_pos[0]-=1
      elif action==1:
         new_pos[0]+=1
      elif action==2:
         new_pos[1]-=1
      elif action==3:
         new_pos[1]+=1
    
      if self._is_valid_position(new_pos):
        self.current=new_pos
        x,y=self.current
        cell=[x,y]
    
      if len(self.visited)>=36:
          return self.current,1,True,{}
      x,y=self.current
      cell=[x,y]
      if cell in self.visited:
          reward=-2
          done=False
      else:
       self.visited.append(cell)
       reward=0
       done=False
      return self.current,reward,done,{}

    def discretize_state(self, state):
        return state[0] * self.n_states + state[1]
      
        

    def _is_valid_position(self,pos):
      row,col=pos
      if row<0 or col<0 or row>= self.rows or col >=self.cols:
        return False
      if self.room[row,col]=='1':
       return False
      return True

    def render(self):
      self.screen.fill((255, 255, 255))
      for row in range(self.rows):
          for col in range(self.cols):
              cell_left = col * self.cell_size
              cell_top = row * self.cell_size

              if self.room[row, col] == '1':
                  pygame.draw.rect(self.screen, (0, 0, 0), (cell_left, cell_top, self.cell_size, self.cell_size))
              elif self.room[row, col] == 'S':
                  pygame.draw.rect(self.screen, (10, 122, 40), (cell_left, cell_top, self.cell_size, self.cell_size))
              elif self.room[row, col] == 'G':
                  pygame.draw.rect(self.screen, (145, 74, 19), (cell_left, cell_top, self.cell_size, self.cell_size))
              elif self.room[row, col] == 'G':
                  pygame.draw.rect(self.screen, (145, 74, 19), (cell_left, cell_top, self.cell_size, self.cell_size))                
              if np.array_equal(np.array(self.current), np.array([row, col]).reshape(-1,1)):
                  pygame.draw.circle(self.screen, (0, 0, 255), (cell_left + self.cell_size // 2, cell_top + self.cell_size // 2), self.cell_size // 2)
      pygame.display.update()


In [7]:
# Create the gym environment
env = VacEnv()
# Define the Q-table

try:
    df=pd.read_csv('vaccum_q_table')
    df=df.drop(0)
    q_table=df.to_numpy()
except:
    q_table = np.zeros([250, 4])
# Define the hyperparameters
learning_rate = 0.4
discount_factor = 0.6
epsilon = 0.7
num_episodes = 1
pygame.init()
# Q-learning algorithm
for episode in range(num_episodes):
    env.visited=[]
    state = env.reset()
    state = env.discretize_state(state)[0]
    done = False
    for event in pygame.event.get():  # process events to keep the window responsive
        if event.type == pygame.QUIT:
            pygame.quit()
            quit()
    while not done:
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                pygame.quit()
                quit()
        if np.random.uniform(0, 1) < epsilon:
            action = env.action_space.sample()
        else:
            action = np.argmax(q_table[state])
        next_state, reward, done, _ = env.step(action)
        next_state = env.discretize_state(next_state)[0]
        q_table[state][action] = (1 - learning_rate) * q_table[state][action] + learning_rate * (reward + discount_factor * np.max(q_table[next_state]))
        state = next_state
        env.render()
        pygame.time.delay(50)  # introducing a delay to slow down the rendering
        env.clock.tick(60)
        # printing the current state of the environment
        print("Episode:", episode+1)
        #display_environment(state)
        print("Action:", action)
        print("Next State:", next_state)
        print("Reward:", reward)
        print("Q-table:")
        print(q_table)
        print("--------------------")
# printing the Q table
print("Q table:")
print(q_table)
df=pd.DataFrame(q_table)
df.to_csv('vaccum_q_table',index=False)
print('saved to csv file')

Episode: 1
Action: 2
Next State: 0
Reward: 0
Q-table:
[[-4.38647477 -4.12596657 -3.42581728 -4.2198278 ]
 [-4.58177502 -4.57969425 -4.62803788 -4.65024264]
 [-4.03947393 -3.04122352 -4.6342471  -4.21457411]
 [-4.49173009 -4.27378758 -4.52313308 -3.78409115]
 [-4.45708579 -4.25424112 -4.193883   -3.72324358]
 [-4.62322662 -3.87930288 -4.48516273 -4.59267908]
 [-4.66384243 -4.59842972 -4.58136946 -4.66633292]
 [-4.60073086 -4.63422305 -4.61630259 -3.35904809]
 [-4.68295326 -4.71548217 -3.91277286 -4.73216283]
 [-0.8        -0.8        -1.11870919  0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0.          0.        ]
 [ 0.          0.          0

error: display Surface quit

: 